In [76]:
import pandas as pd
import numpy as np
import json

In [77]:
songs_df = pd.read_csv('final_cleaned.csv')
print(df.shape)

(13640, 7)


In [78]:
df.head()

id                                             lyrics  \
0  4575103  [Chorus: Ed Sheeran]\nOh, I been on for a thou...   
1  3541694  [Verse 1]\nI will always remember\nThe day you...   
2  7120781  [Verse 1]\nI had a bad week\nSpent the evening...   
3  7921365  [Verse 1: Ed Sheeran]\nI had a bad week\nSpent...   
4   493576  [Verse 1]\nI think I took too much\nI'm addict...   

                                          annotation      artist  artist_id  \
0  “1000 Nights” is a collaboration between Ed Sh...  Ed Sheeran      12418   
1  In “2002,” Anne-Marie reminisces about falling...  Ed Sheeran      12418   
2  In an upbeat switch of tone, “2step” is Ed She...  Ed Sheeran      12418   
3  “2step (Remix)” is the fifth single from Ed Sh...  Ed Sheeran      12418   
4  Ed mentions in the Part 2 of his tour diary th...  Ed Sheeran      12418   

            song                                            prompts  
0    1000 Nights  Write me a song called 1000 Nights with the fo...  
1           2002  Write me a song called 2002 with the following...  
2          2step  Write me a song called 2step with the followin...  
3  2step (Remix)  Write me a song called 2step (Remix) with the ...  
4       Addicted  Write me a song called Addicted with the follo...

In [79]:
def create_prompts_table(data, pre_text, post_text):
    pre_prompt = pre_text
    main_prompt = data['annotation']
    post_prompt = post_text
    full_prompt = pre_prompt + main_prompt + post_prompt
    return full_prompt

In [80]:
#create a sampel prompts table
pre = pd.DataFrame(["Write me a song called "] * songs_df.shape[0])[0] + songs_df['song'] + ' with the following description: '
post = pd.DataFrame([" Make sure the lyrics are different from the original song."] * songs_df.shape[0])[0]
prompt = create_prompts_table(songs_df, pre, post)
prompts_df = pd.DataFrame({'prompts': prompt})
prompts_df.head()

prompts
0  Write me a song called 1000 Nights with the fo...
1  Write me a song called 2002 with the following...
2  Write me a song called 2step with the followin...
3  Write me a song called 2step (Remix) with the ...
4  Write me a song called Addicted with the follo...

In [81]:
prompts_df['prompts'][0]

'Write me a song called 1000 Nights with the following description: “1000 Nights” is a collaboration between Ed Sheeran, Meek Mill, and A Boogie wit da Hoodie that appears on Ed’s No.6 Collaborations Project. On the track, the artists discuss touring the world and boast about the perks of being rich and famous.\nThis songs marks the first time any of these artists have collaborated. Make sure the lyrics are different from the original song.'

In [82]:
songs_df["prompts"] = prompts_df["prompts"]
songs_df.head()

id                                             lyrics  \
0  4575103  [Chorus: Ed Sheeran]\nOh, I been on for a thou...   
1  3541694  [Verse 1]\nI will always remember\nThe day you...   
2  7120781  [Verse 1]\nI had a bad week\nSpent the evening...   
3  7921365  [Verse 1: Ed Sheeran]\nI had a bad week\nSpent...   
4   493576  [Verse 1]\nI think I took too much\nI'm addict...   

                                          annotation      artist  artist_id  \
0  “1000 Nights” is a collaboration between Ed Sh...  Ed Sheeran      12418   
1  In “2002,” Anne-Marie reminisces about falling...  Ed Sheeran      12418   
2  In an upbeat switch of tone, “2step” is Ed She...  Ed Sheeran      12418   
3  “2step (Remix)” is the fifth single from Ed Sh...  Ed Sheeran      12418   
4  Ed mentions in the Part 2 of his tour diary th...  Ed Sheeran      12418   

            song                                            prompts  
0    1000 Nights  Write me a song called 1000 Nights with the fo...  
1           2002  Write me a song called 2002 with the following...  
2          2step  Write me a song called 2step with the followin...  
3  2step (Remix)  Write me a song called 2step (Remix) with the ...  
4       Addicted  Write me a song called Addicted with the follo...

In [83]:
def convert_table_to_conversation(data):
    result = []
    for i in range(data.shape[0]):
        row = data.loc[i]
        outer_dict = {}
        outer_dict["id"] = i
        outer_dict["conversations"] = []
        conversations = outer_dict["conversations"]
        conversations.append({"from":"human", "value":row["prompts"]})
        conversations.append({"from":"gpt", "value":row["lyrics"]})
        result.append(outer_dict)
    return result

In [84]:
convo = convert_table_to_conversation(songs_df)
convo_json = json.dumps(convo, indent=2)

In [85]:
print(convo_json[0:100000])

[
  {
    "id": 0,
    "conversations": [
      {
        "from": "human",
        "value": "Write me a song called 1000 Nights with the following description: \u201c1000 Nights\u201d is a collaboration between Ed Sheeran, Meek Mill, and A Boogie wit da Hoodie that appears on Ed\u2019s No.6 Collaborations Project. On the track, the artists discuss touring the world and boast about the perks of being rich and famous.\nThis songs marks the first time any of these artists have collaborated. Make sure the lyrics are different from the original song."
      },
      {
        "from": "gpt",
        "value": "[Chorus: Ed Sheeran]\nOh, I been on for a thousand nights\nNew York to London, different city every day, yeah\nPlayin' on, playin' on, puttin' up 50 thousand lights\nOh, I've been gone so long, gettin' up and gettin' faded\nSo I'm on, keepin' on, stayin' up for a thousand nights\n[Verse 1: Meek Mill]\nThis the type of shit we used to dream of (Yeah, yeah)\nBad bitch look like Mona Lisa 

In [86]:
# Write convo to conversation_style.json
with open("conversation_style.json", "w") as outfile:
    outfile.write(convo_json)